In [1]:
import os
os.environ['PYTHONHASHSEED']=str(0)

In [2]:
"""
Coin Game environment.
"""
import sys
import gym
import pylab
import random
import tensorflow as tf
import numpy as np
from keras.layers import Dense
from keras.models import Sequential
from keras.optimizers import Adam
from keras import backend as K

from gym.spaces import Discrete, Tuple
from gym.spaces import prng


np.random.seed(123)
random.seed(456)
prng.seed(456)

session_conf = tf.ConfigProto(intra_op_parallelism_threads=1, inter_op_parallelism_threads=1)


tf.set_random_seed(789)

sess = tf.Session(graph=tf.get_default_graph(), config=session_conf)
K.set_session(sess)


class CoinGameVec:
    """
    Vectorized Coin Game environment.
    Note: slightly deviates from the Gym API.
    """
    NUM_AGENTS = 2
    NUM_ACTIONS = 4
    MOVES = [
        np.array([0,  1]),
        np.array([0, -1]),
        np.array([1,  0]),
        np.array([-1, 0]), 
    ]

    def __init__(self, max_steps = 10, batch_size = 1, grid_size=3):
        self.max_steps = max_steps
        self.grid_size = grid_size
        self.batch_size = batch_size
        # The 4 channels stand for 2 players and 2 coin positions
        self.ob_space_shape = [4, grid_size, grid_size]

        self.step_count = None

    def reset(self):
        self.step_count = 0
        self.red_coin = prng.np_random.randint(2, size=self.batch_size)
        # Agent and coin positions
        self.red_pos  = prng.np_random.randint(
            self.grid_size, size=(self.batch_size, 2))
        self.blue_pos = prng.np_random.randint(
            self.grid_size, size=(self.batch_size, 2))
        self.coin_pos = np.zeros((self.batch_size, 2), dtype=np.int8)
        for i in range(self.batch_size):
            # Make sure coins don't overlap
            while self._same_pos(self.red_pos[i], self.blue_pos[i]):
                self.blue_pos[i] = prng.np_random.randint(self.grid_size, size=2)
            self._generate_coin(i)
        return self._generate_state()

    def _generate_coin(self, i):
        self.red_coin[i] = 1 - self.red_coin[i]
        # Make sure coin has a different position than the agents
        success = 0
        while success < 2:
            self.coin_pos[i] = prng.np_random.randint(self.grid_size, size=(2))
            success  = 1 - self._same_pos(self.red_pos[i],
                                          self.coin_pos[i])
            success += 1 - self._same_pos(self.blue_pos[i],
                                          self.coin_pos[i])

    def _same_pos(self, x, y):
        return (x == y).all()

    def _generate_state(self):
        state = np.zeros([self.batch_size] + self.ob_space_shape)
        for i in range(self.batch_size):
            state[i, 0, self.red_pos[i][0], self.red_pos[i][1]] = 1
            state[i, 1, self.blue_pos[i][0], self.blue_pos[i][1]] = 1
            if self.red_coin[i]:
                state[i, 2, self.coin_pos[i][0], self.coin_pos[i][1]] = 1
            else:
                state[i, 3, self.coin_pos[i][0], self.coin_pos[i][1]] = 1
        return state

    def step(self, action1, action2):
        for j in range(self.batch_size):
            ac0 = action1
            ac1 = action2
            assert ac0 in {0, 1, 2, 3} and ac1 in {0, 1, 2, 3}

            # Move players
            self.red_pos[j] = \
                (self.red_pos[j] + self.MOVES[ac0]) % self.grid_size
            self.blue_pos[j] = \
                (self.blue_pos[j] + self.MOVES[ac1]) % self.grid_size

        # Compute rewards
        reward_red, reward_blue = [], []
        for i in range(self.batch_size):
            generate = False
            if self.red_coin[i]:
                if self._same_pos(self.red_pos[i], self.coin_pos[i]):
                    generate = True
                    reward_red.append(0)
                    reward_blue.append(0)
                elif self._same_pos(self.blue_pos[i], self.coin_pos[i]):
                    generate = True
                    reward_red.append(0)
                    reward_blue.append(1)
                else:
                    reward_red.append(1)
                    reward_blue.append(0)

            else:
                if self._same_pos(self.blue_pos[i], self.coin_pos[i]):
                    generate = True
                    reward_red.append(0)
                    reward_blue.append(0)
                elif self._same_pos(self.red_pos[i], self.coin_pos[i]):
                    generate = True
                    reward_red.append(0)
                    reward_blue.append(1)

                else:
                    reward_red.append(1)
                    reward_blue.append(0)

            #if generate:
                #self._generate_coin(i)

        reward = [np.array(reward_red), np.array(reward_blue)]
        self.step_count += 1
        state = self._generate_state()

        return state, reward, generate

class A2CAgent:
    def __init__(self, state_size, action_size):
        # if you want to see Cartpole learning, then change to True
        self.render = False
        self.load_model = False
        # get size of state and action
        self.state_size = state_size
        self.action_size = action_size
        self.value_size = 1
        #self.action_table = [0,1,-4,4]
        self.lam = 0
        self.alpha = 0.2
        #self.target_state = 11

        # These are hyper parameters for the Policy Gradient
        self.discount_factor = 1
        self.actor_lr = 0.005
        self.critic_lr = 0.005

        # create model for policy network
        self.actor = self.build_actor()        
        self.critic = self.build_critic()
        self.critic2 = self.build_critic2()

        #if self.load_model:
            #self.actor.load_weights("./save_model/cartpole_actor.h5")
            #self.critic.load_weights("./save_model/cartpole_critic.h5")

    # approximate policy and value using Neural Network
    # actor: state is input and probability of each action is output of model
    def build_actor(self):
        actor = Sequential()
        actor.add(Dense(48, input_dim=self.state_size, activation='relu',
                        kernel_initializer='he_uniform'))
        #actor.add(Dense(16, activation='relu',
                        #kernel_initializer='he_uniform'))
        actor.add(Dense(self.action_size, activation='softmax',
                        kernel_initializer='he_uniform'))
        actor.summary()
        # See note regarding crossentropy in cartpole_reinforce.py
        actor.compile(loss='categorical_crossentropy',
                      optimizer=Adam(lr=self.actor_lr))
        return actor

    # critic: state is input and value of state is output of model
    def build_critic(self):
        critic = Sequential()
        critic.add(Dense(48, input_dim=self.state_size, activation='relu',
                         kernel_initializer='he_uniform'))
        #critic.add(Dense(16, activation='relu',
                         #kernel_initializer='he_uniform'))
        critic.add(Dense(self.value_size, activation='linear',
                         kernel_initializer='he_uniform'))
        #critic.summary()
        critic.compile(loss="mse", optimizer=Adam(lr=self.critic_lr))
        return critic
    
    def build_critic2(self):
        critic = Sequential()
        critic.add(Dense(48, input_dim=self.state_size, activation='relu',
                         kernel_initializer='he_uniform'))
        #critic.add(Dense(16, activation='relu',
                         #kernel_initializer='he_uniform'))
        critic.add(Dense(self.value_size, activation='linear',
                         kernel_initializer='he_uniform'))
        #critic.summary()
        critic.compile(loss="mse", optimizer=Adam(lr=self.critic_lr))
        return critic
        

    # using the output of policy network, pick action stochastically
    def get_action(self, state):
        policy = self.actor.predict(state, batch_size=1).flatten()
        return np.random.choice(self.action_size, 1, p=policy)[0]
    
    def get_maxaction(self,state):
        policy = self.actor.predict(state, batch_size=1).flatten()
        return np.argmax(policy)

    # update policy network every episode
    def train_model(self, state, action, reward1,reward2, next_state, done):
        target = np.zeros((1, self.value_size))
        advantages = np.zeros((1, self.action_size))
        target2 = np.zeros((1, self.value_size))     

        value = self.critic.predict(state)[0]
        value2 = self.critic2.predict(state)[0]
        next_value = self.critic.predict(next_state)[0]
        next_value2 = self.critic2.predict(next_state)[0]
        
        reward1 = reward1 + self.lam*(reward2 - self.alpha)

        if done:
            advantages[0][action] = -1*(reward1 - value)
            target[0][0] = reward1
            target2[0][0] = reward2
        else:
            advantages[0][action] = -1*(reward1 + self.discount_factor * (next_value) - value)
            target[0][0] = reward1 + self.discount_factor * next_value
            target2[0][0] = reward2 + self.discount_factor * next_value2
#             if np.where(next_state == 1.0)[1][0] == self.target_state:
#                 target2[0][0] = 0 + self.discount_factor * next_value2
#             else:
#                 target2[0][0] = np.where(next_state == 1.0)[1][0]/10 + self.discount_factor * next_value2            
            

        self.actor.fit(state, advantages, epochs=1, verbose=0)
        self.critic.fit(state, target, epochs=1, verbose=0)
        self.critic2.fit(state,target2,epochs = 1, verbose = 0)
        
        #initial_state = np.zeros((1,state_size))
        #initial_state[0][0] = 1
        self.lam = min(max(0,(self.lam + 0.001*(self.critic2.predict(state)[0] - self.alpha))), 10)
        #print(self.lam)
        

if __name__ == "__main__":
    # In case of CartPole-v1, maximum length of episode is 500
    #env = gym.make('CartPole-v1')
    # get size of state and action from environment
    state_size = 4*3*3 #env.observation_space.shape[0]
    action_size = 4 #env.action_space.n
    EPISODES = 10000

    
    
    # make A2C agent
    agent1 = A2CAgent(state_size, action_size)
    agent2 = A2CAgent(state_size,action_size)
    game = CoinGameVec()
    
    average_penalty = 0
    total_penalty = 0
    store_penalty = np.zeros((1,EPISODES))
        
    average_lag = 0
    total_lag = 0
    store_lag = np.zeros((1,EPISODES))

    
    scores, episodes = [], []

    for i in range(1):
        done = False
        score = 0
        #state = env.reset()
        #state = np.reshape(state, [1, state_size])
        #rand_state = random.randint(0,15)
        #state = np.zeros((1,state_size))
        #state[0][rand_state] = 1
        #state = np.reshape(state, [1, state_size])
        
        for e in range(EPISODES):
        #state = env.reset()
            state = game.reset()
            state = np.reshape(state, [1, state_size])
            for time in range(10):
            # env.render()
                action1 = agent1.get_action(state)
                action2 = agent2.get_action(state)
                
                next_state, reward, done = game.step(action1,action2)
                
            #reward = reward if not done else -10
                next_state = np.reshape(next_state, [1, state_size])
                agent1.train_model(state, action1, reward[0][0],reward[1][0],next_state, done)
                agent2.train_model(state, action2, reward[0][0],reward[1][0],next_state, done)
                
                
                print(np.where(state == 1.0)[1][0],np.where(state == 1.0)[1][1] - 9,np.where(state == 1.0)[1][2],"--",action1, action2,"--",reward[0][0],reward[1][0],"--",np.where(next_state == 1.0)[1][0],np.where(next_state == 1.0)[1][1] - 9,np.where(next_state == 1.0)[1][2])
                
                #print(agent1.lam,agent2.lam)
                state = next_state
                
                average_penalty = average_penalty + reward[1][0]
                average_lag = average_lag + reward[0][0]
                
                if done:
                #print(state)
                    print("episode: {}/{}, score: {}"
                      .format(e, EPISODES, time))
                    print(agent1.lam)
                    print(agent2.lam)
                    break
                #if len(agent.memory) > batch_size:
                    #agent.replay(batch_size)
                    
            total_penalty = total_penalty + average_penalty        
            store_penalty[0][e] = total_penalty/(e+1) 
            print(store_penalty[0][e])
                
            total_lag = total_lag + average_lag
            store_lag[0][e] = total_lag/(e+1)
                
                #if np.mean(store_penalty[0][e-100:e]) < agent.alpha+0.1:
                        #sys.exit()
                #print(store_penalty[0][e])
            average_penalty = 0
            average_lag = 0
        
            print('*******************************')
    

/home/raghuram/anaconda3/lib/python3.6/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
Using TensorFlow backend.


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_1 (Dense)              (None, 48)                1776      
_________________________________________________________________
dense_2 (Dense)              (None, 4)                 196       
Total params: 1,972
Trainable params: 1,972
Non-trainable params: 0
_________________________________________________________________
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_7 (Dense)              (None, 48)                1776      
_________________________________________________________________
dense_8 (Dense)              (None, 4)                 196       
Total params: 1,972
Trainable params: 1,972
Non-trainable params: 0
_________________________________________________________________
4 6 35 -- 2 1 -- 0 0 -- 7 8 35
episode: 0/10000, score: 0
0
[0.00041478]

4 8 27 -- 3 3 -- 1 0 -- 1 5 27
1 5 27 -- 3 3 -- 1 0 -- 7 2 27
7 2 27 -- 1 3 -- 1 0 -- 6 8 27
6 8 27 -- 0 3 -- 1 0 -- 7 5 27
7 5 27 -- 0 3 -- 1 0 -- 8 2 27
8 2 27 -- 3 3 -- 1 0 -- 5 8 27
5 8 27 -- 0 1 -- 1 0 -- 3 7 27
3 7 27 -- 0 1 -- 1 0 -- 4 6 27
4 6 27 -- 0 0 -- 1 0 -- 5 7 27
0.36363636363636365
*******************************
2 3 35 -- 0 3 -- 1 0 -- 0 0 35
0 0 35 -- 0 1 -- 1 0 -- 1 2 35
1 2 35 -- 0 1 -- 1 0 -- 2 1 35
2 1 35 -- 0 1 -- 1 0 -- 0 0 35
0 0 35 -- 0 1 -- 1 0 -- 1 2 35
1 2 35 -- 0 3 -- 0 0 -- 2 8 35
episode: 33/10000, score: 5
[0.01859382]
[0.03892999]
0.35294117647058826
*******************************
7 1 23 -- 0 3 -- 1 0 -- 8 7 23
8 7 23 -- 1 1 -- 1 0 -- 7 6 23
7 6 23 -- 0 1 -- 1 0 -- 8 8 23
8 8 23 -- 3 1 -- 0 0 -- 5 7 23
episode: 34/10000, score: 3
[0.01847588]
[0.04070622]
0.34285714285714286
*******************************
1 7 32 -- 0 1 -- 1 0 -- 2 6 32
2 6 32 -- 0 3 -- 1 0 -- 0 3 32
0 3 32 -- 0 3 -- 1 0 -- 1 0 32
1 0 32 -- 2 3 -- 1 0 -- 4 6 32
4 6 32 -- 2 2 -- 1 0 --

4 6 28 -- 3 2 -- 0 1 -- 1 0 28
episode: 68/10000, score: 0
[0.04428871]
[0.07564836]
0.391304347826087
*******************************
3 2 33 -- 3 1 -- 1 0 -- 0 1 33
0 1 33 -- 0 0 -- 1 0 -- 1 2 33
1 2 33 -- 0 0 -- 1 0 -- 2 0 33
2 0 33 -- 3 0 -- 1 0 -- 8 1 33
8 1 33 -- 3 3 -- 1 0 -- 5 7 33
5 7 33 -- 0 0 -- 1 0 -- 3 8 33
3 8 33 -- 3 3 -- 1 0 -- 0 5 33
0 5 33 -- 3 0 -- 0 1 -- 6 3 33
episode: 69/10000, score: 7
[0.04496373]
[0.07740842]
0.4
*******************************
4 8 18 -- 3 1 -- 1 0 -- 1 7 18
1 7 18 -- 3 3 -- 1 0 -- 7 4 18
7 4 18 -- 3 0 -- 1 0 -- 4 5 18
4 5 18 -- 3 1 -- 1 0 -- 1 4 18
1 4 18 -- 0 0 -- 1 0 -- 2 5 18
2 5 18 -- 3 0 -- 1 0 -- 8 3 18
8 3 18 -- 3 3 -- 0 1 -- 5 0 18
episode: 70/10000, score: 6
[0.04765718]
[0.07995755]
0.4084507042253521
*******************************
6 8 32 -- 3 1 -- 1 0 -- 3 7 32
3 7 32 -- 3 3 -- 1 0 -- 0 4 32
0 4 32 -- 3 0 -- 0 0 -- 6 5 32
episode: 71/10000, score: 2
[0.04844255]
[0.08096492]
0.4027777777777778
*******************************
2 8 28 

1 4 33 -- 3 3 -- 1 0 -- 7 1 33
7 1 33 -- 3 2 -- 1 0 -- 4 4 33
4 4 33 -- 1 2 -- 1 0 -- 3 7 33
3 7 33 -- 3 2 -- 1 0 -- 0 1 33
0 1 33 -- 3 2 -- 0 1 -- 6 4 33
episode: 103/10000, score: 4
[0.07654119]
[0.10701272]
0.38461538461538464
*******************************
1 7 27 -- 3 3 -- 1 0 -- 7 4 27
7 4 27 -- 3 0 -- 1 0 -- 4 5 27
4 5 27 -- 3 0 -- 1 0 -- 1 3 27
1 3 27 -- 1 2 -- 0 1 -- 0 6 27
episode: 104/10000, score: 3
[0.07786045]
[0.10786476]
0.3904761904761905
*******************************
6 4 28 -- 0 0 -- 1 0 -- 7 5 28
7 5 28 -- 3 0 -- 1 0 -- 4 3 28
4 3 28 -- 3 2 -- 0 1 -- 1 6 28
episode: 105/10000, score: 2
[0.07925924]
[0.10933284]
0.39622641509433965
*******************************
3 5 18 -- 3 0 -- 0 0 -- 0 3 18
episode: 106/10000, score: 0
[0.07967281]
[0.10971418]
0.3925233644859813
*******************************
8 2 19 -- 1 0 -- 1 0 -- 7 0 19
7 0 19 -- 0 2 -- 1 0 -- 8 3 19
8 3 19 -- 3 2 -- 1 0 -- 5 6 19
5 6 19 -- 0 0 -- 1 0 -- 3 7 19
3 7 19 -- 3 2 -- 0 1 -- 0 1 19
episode: 107/100

...

8 6 29 -- 0 0 -- 1 0 -- 6 7 29
6 7 29 -- 0 0 -- 1 0 -- 7 8 29
7 8 29 -- 0 2 -- 0 0 -- 8 2 29
episode: 9785/10000, score: 3
[2.07531]
[2.092049]
0.29848763539750667
*******************************
8 6 22 -- 3 0 -- 1 0 -- 5 7 22
5 7 22 -- 0 2 -- 1 0 -- 3 1 22
3 1 22 -- 3 2 -- 0 1 -- 0 4 22
episode: 9786/10000, score: 2
[2.0756671]
[2.0924418]
0.29855931337488506
*******************************
5 6 27 -- 0 0 -- 1 0 -- 3 7 27
3 7 27 -- 3 0 -- 0 1 -- 0 8 27
episode: 9787/10000, score: 1
[2.0773995]
[2.094049]
0.29863097670617084
*******************************
0 2 32 -- 1 3 -- 1 0 -- 2 8 32
2 8 32 -- 0 3 -- 0 0 -- 0 5 32
episode: 9788/10000, score: 1
[2.0771937]
[2.0937028]
0.29860046991521094
*******************************
7 4 30 -- 3 0 -- 1 0 -- 4 5 30
4 5 30 -- 3 0 -- 0 0 -- 1 3 30
episode: 9789/10000, score: 1
[2.076839]
[2.0933545]
0.2985699693564862
*******************************
3 5 27 -- 3 0 -- 0 1 -- 0 3 27
episode: 9790/10000, score: 0
[2.0775836]
[2.0942063]
0.2986416096415075


0 3 25 -- 3 2 -- 1 0 -- 6 6 25
6 6 25 -- 0 0 -- 0 0 -- 7 7 25
episode: 9835/10000, score: 3
[2.0720956]
[2.0866027]
0.2980886539243595
*******************************
3 1 27 -- 3 0 -- 0 1 -- 0 2 27
episode: 9836/10000, score: 0
[2.0725005]
[2.0873563]
0.2981600081325607
*******************************
3 8 25 -- 3 0 -- 1 0 -- 0 6 25
0 6 25 -- 3 0 -- 0 1 -- 6 7 25
episode: 9837/10000, score: 1
[2.0734174]
[2.088596]
0.2982313478349258
*******************************
5 6 22 -- 0 0 -- 1 0 -- 3 7 22
3 7 22 -- 3 2 -- 1 0 -- 0 1 22
0 1 22 -- 3 2 -- 0 1 -- 6 4 22
episode: 9838/10000, score: 2
[2.0744278]
[2.0895588]
0.29830267303587765
*******************************
1 4 24 -- 3 0 -- 1 0 -- 7 5 24
7 5 24 -- 0 0 -- 1 0 -- 8 3 24
8 3 24 -- 0 2 -- 0 0 -- 6 6 24
episode: 9839/10000, score: 2
[2.0746727]
[2.089795]
0.29827235772357724
*******************************
4 1 27 -- 1 0 -- 1 0 -- 3 2 27
3 2 27 -- 3 0 -- 0 0 -- 0 0 27
episode: 9840/10000, score: 1
[2.0744715]
[2.0897214]
0.2982420485722996

8 3 33 -- 3 2 -- 0 0 -- 5 6 33
episode: 9885/10000, score: 0
[2.0645683]
[2.0818236]
0.29769370827432734
*******************************
6 5 25 -- 0 0 -- 0 0 -- 7 3 25
episode: 9886/10000, score: 0
[2.0644119]
[2.0816152]
0.29766359866491354
*******************************
5 1 18 -- 3 0 -- 1 0 -- 2 2 18
2 2 18 -- 0 3 -- 0 0 -- 0 8 18
episode: 9887/10000, score: 1
[2.0640028]
[2.081311]
0.2976334951456311
*******************************
1 6 21 -- 2 0 -- 1 0 -- 4 7 21
4 7 21 -- 1 3 -- 0 0 -- 3 4 21
episode: 9888/10000, score: 1
[2.0636597]
[2.081074]
0.2976033977146324
*******************************
0 1 29 -- 3 0 -- 0 0 -- 6 2 29
episode: 9889/10000, score: 0
[2.0634751]
[2.0808964]
0.2975733063700708
*******************************
6 7 29 -- 0 0 -- 1 0 -- 7 8 29
7 8 29 -- 0 2 -- 0 0 -- 8 2 29
episode: 9890/10000, score: 1
[2.0630016]
[2.0804129]
0.29754322111010006
*******************************
8 6 20 -- 3 0 -- 1 0 -- 5 7 20
5 7 20 -- 3 3 -- 0 0 -- 2 4 20
episode: 9891/10000, score: 

0 4 35 -- 0 0 -- 1 0 -- 1 5 35
1 5 35 -- 0 0 -- 1 0 -- 2 3 35
2 3 35 -- 0 2 -- 1 0 -- 0 6 35
0 6 35 -- 0 0 -- 1 0 -- 1 7 35
1 7 35 -- 0 0 -- 0 0 -- 2 8 35
episode: 9934/10000, score: 4
[2.053942]
[2.0726764]
0.2969300452944137
*******************************
6 2 25 -- 0 0 -- 0 0 -- 7 0 25
episode: 9935/10000, score: 0
[2.0538306]
[2.072491]
0.2969001610305958
*******************************
1 5 20 -- 0 0 -- 0 0 -- 2 3 20
episode: 9936/10000, score: 0
[2.0537417]
[2.0723524]
0.2968702827815236
*******************************
2 3 24 -- 0 2 -- 0 1 -- 0 6 24
episode: 9937/10000, score: 0
[2.0546675]
[2.0732675]
0.29694103441336284
*******************************
7 6 29 -- 0 0 -- 1 0 -- 8 7 29
8 7 29 -- 0 0 -- 1 0 -- 6 8 29
6 8 29 -- 0 2 -- 0 0 -- 7 2 29
episode: 9938/10000, score: 2
[2.0542874]
[2.0727298]
0.29691115806419155
*******************************
4 8 20 -- 3 2 -- 0 1 -- 1 2 20
episode: 9939/10000, score: 0
[2.054897]
[2.073061]
0.29698189134808856
*******************************

5 4 30 -- 3 0 -- 1 0 -- 2 5 30
2 5 30 -- 0 0 -- 0 0 -- 0 3 30
episode: 9981/10000, score: 2
[2.04649]
[2.0626967]
0.29623321979563216
*******************************
2 0 32 -- 0 2 -- 1 0 -- 0 3 32
0 3 32 -- 1 2 -- 1 0 -- 2 6 32
2 6 32 -- 0 0 -- 1 0 -- 0 7 32
0 7 32 -- 3 3 -- 1 0 -- 6 4 32
6 4 32 -- 3 0 -- 0 0 -- 3 5 32
episode: 9982/10000, score: 4
[2.0453138]
[2.0617294]
0.296203546028248
*******************************
8 5 22 -- 3 0 -- 1 0 -- 5 3 22
5 3 22 -- 3 2 -- 1 0 -- 2 6 22
2 6 22 -- 0 0 -- 1 0 -- 0 7 22
0 7 22 -- 3 0 -- 1 0 -- 6 8 22
6 8 22 -- 0 2 -- 1 0 -- 7 2 22
7 2 22 -- 3 2 -- 0 0 -- 4 5 22
episode: 9983/10000, score: 5
[2.0451496]
[2.0610654]
0.2961738782051282
*******************************
7 2 26 -- 0 2 -- 0 0 -- 8 5 26
episode: 9984/10000, score: 0
[2.044927]
[2.060893]
0.29614421632448673
*******************************
8 2 21 -- 3 3 -- 1 0 -- 5 8 21
5 8 21 -- 0 3 -- 0 0 -- 3 5 21
episode: 9985/10000, score: 1
[2.044527]
[2.060544]
0.2961145603845384
****************

In [5]:
class A2CAgent:
    def __init__(self, state_size, action_size):
        # if you want to see Cartpole learning, then change to True
        self.render = False
        self.load_model = False
        # get size of state and action
        self.state_size = state_size
        self.action_size = action_size
        self.value_size = 1
        #self.action_table = [0,1,-4,4]
        self.lam = 0
        self.alpha = 0.2
        #self.target_state = 11

        # These are hyper parameters for the Policy Gradient
        self.discount_factor = 1
        self.actor_lr = 0.005
        self.critic_lr = 0.005

        # create model for policy network
        self.actor = self.build_actor()        
        self.critic = self.build_critic()
        self.critic2 = self.build_critic2()

        #if self.load_model:
            #self.actor.load_weights("./save_model/cartpole_actor.h5")
            #self.critic.load_weights("./save_model/cartpole_critic.h5")

    # approximate policy and value using Neural Network
    # actor: state is input and probability of each action is output of model
    def build_actor(self):
        actor = Sequential()
        actor.add(Dense(48, input_dim=self.state_size, activation='relu',
                        kernel_initializer='he_uniform'))
        #actor.add(Dense(16, activation='relu',
                        #kernel_initializer='he_uniform'))
        actor.add(Dense(self.action_size, activation='softmax',
                        kernel_initializer='he_uniform'))
        actor.summary()
        # See note regarding crossentropy in cartpole_reinforce.py
        actor.compile(loss='categorical_crossentropy',
                      optimizer=Adam(lr=self.actor_lr))
        return actor

    # critic: state is input and value of state is output of model
    def build_critic(self):
        critic = Sequential()
        critic.add(Dense(48, input_dim=self.state_size, activation='relu',
                         kernel_initializer='he_uniform'))
        #critic.add(Dense(16, activation='relu',
                         #kernel_initializer='he_uniform'))
        critic.add(Dense(self.value_size, activation='linear',
                         kernel_initializer='he_uniform'))
        #critic.summary()
        critic.compile(loss="mse", optimizer=Adam(lr=self.critic_lr))
        return critic
    
    def build_critic2(self):
        critic = Sequential()
        critic.add(Dense(48, input_dim=self.state_size, activation='relu',
                         kernel_initializer='he_uniform'))
        #critic.add(Dense(16, activation='relu',
                         #kernel_initializer='he_uniform'))
        critic.add(Dense(self.value_size, activation='linear',
                         kernel_initializer='he_uniform'))
        #critic.summary()
        critic.compile(loss="mse", optimizer=Adam(lr=self.critic_lr))
        return critic
        

    # using the output of policy network, pick action stochastically
    def get_action(self, state):
        policy = self.actor.predict(state, batch_size=1).flatten()
        return np.random.choice(self.action_size, 1, p=policy)[0]
    
    def get_maxaction(self,state):
        policy = self.actor.predict(state, batch_size=1).flatten()
        return np.argmax(policy)

    # update policy network every episode
    def train_model(self, state, action, reward1,reward2, next_state, done):
        target = np.zeros((1, self.value_size))
        advantages = np.zeros((1, self.action_size))
        target2 = np.zeros((1, self.value_size))     

        value = self.critic.predict(state)[0]
        value2 = self.critic2.predict(state)[0]
        next_value = self.critic.predict(next_state)[0]
        next_value2 = self.critic2.predict(next_state)[0]
        
        reward1 = reward1 + self.lam*(reward2 - self.alpha)

        if done:
            advantages[0][action] = -1*(reward1 - value)
            target[0][0] = reward1
            target2[0][0] = reward2
        else:
            advantages[0][action] = -1*(reward1 + self.discount_factor * (next_value) - value)
            target[0][0] = reward1 + self.discount_factor * next_value
            target2[0][0] = reward2 + self.discount_factor * next_value2
#             if np.where(next_state == 1.0)[1][0] == self.target_state:
#                 target2[0][0] = 0 + self.discount_factor * next_value2
#             else:
#                 target2[0][0] = np.where(next_state == 1.0)[1][0]/10 + self.discount_factor * next_value2            
            

        self.actor.fit(state, advantages, epochs=1, verbose=0)
        self.critic.fit(state, target, epochs=1, verbose=0)
        self.critic2.fit(state,target2,epochs = 1, verbose = 0)
        
        #initial_state = np.zeros((1,state_size))
        #initial_state[0][0] = 1
        self.lam = min(max(0,(self.lam + 0.001*(self.critic2.predict(state)[0] - self.alpha))), 10)
        #print(self.lam)
        

if __name__ == "__main__":
    # In case of CartPole-v1, maximum length of episode is 500
    #env = gym.make('CartPole-v1')
    # get size of state and action from environment
    state_size = 4*3*3 #env.observation_space.shape[0]
    action_size = 4 #env.action_space.n
    EPISODES = 10000

    np.random.seed(123)
    random.seed(456)

    session_conf = tf.ConfigProto(intra_op_parallelism_threads=1, inter_op_parallelism_threads=1)


    tf.set_random_seed(789)

    sess = tf.Session(graph=tf.get_default_graph(), config=session_conf)
    K.set_session(sess)

    
    
    
    # make A2C agent
    agent1 = A2CAgent(state_size, action_size)
    agent2 = A2CAgent(state_size,action_size)
    game = CoinGameVec()
    
    average_penalty = 0
    total_penalty = 0
    store_penalty = np.zeros((1,EPISODES))
        
    average_lag = 0
    total_lag = 0
    store_lag = np.zeros((1,EPISODES))

    
    scores, episodes = [], []

    for i in range(1):
        done = False
        score = 0
        #state = env.reset()
        #state = np.reshape(state, [1, state_size])
        #rand_state = random.randint(0,15)
        #state = np.zeros((1,state_size))
        #state[0][rand_state] = 1
        #state = np.reshape(state, [1, state_size])
        
        for e in range(EPISODES):
        #state = env.reset()
            state = game.reset()
            state = np.reshape(state, [1, state_size])
            for time in range(10):
            # env.render()
                action1 = agent1.get_action(state)
                action2 = agent2.get_action(state)
                
                next_state, reward, done = game.step(action1,action2)
                
            #reward = reward if not done else -10
                next_state = np.reshape(next_state, [1, state_size])
                agent1.train_model(state, action1, reward[0][0],reward[1][0],next_state, done)
                agent2.train_model(state, action2, reward[0][0],reward[1][0],next_state, done)
                
                
                print(np.where(state == 1.0)[1][0],np.where(state == 1.0)[1][1] - 9,np.where(state == 1.0)[1][2],"--",action1, action2,"--",reward[0][0],reward[1][0],"--",np.where(next_state == 1.0)[1][0],np.where(next_state == 1.0)[1][1] - 9,np.where(next_state == 1.0)[1][2])
                
                #print(agent1.lam,agent2.lam)
                state = next_state
                
                average_penalty = average_penalty + reward[1][0]
                average_lag = average_lag + reward[0][0]
                
                if done:
                #print(state)
                    print("episode: {}/{}, score: {}"
                      .format(e, EPISODES, time))
                    print(agent1.lam)
                    print(agent2.lam)
                    break
                #if len(agent.memory) > batch_size:
                    #agent.replay(batch_size)
                    
            total_penalty = total_penalty + average_penalty        
            store_penalty[0][e] = total_penalty/(e+1) 
            print(store_penalty[0][e])
                
            total_lag = total_lag + average_lag
            store_lag[0][e] = total_lag/(e+1)
                
                #if np.mean(store_penalty[0][e-100:e]) < agent.alpha+0.1:
                        #sys.exit()
                #print(store_penalty[0][e])
            average_penalty = 0
            average_lag = 0
        
            print('*******************************')

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_1 (Dense)              (None, 48)                1776      
_________________________________________________________________
dense_2 (Dense)              (None, 4)                 196       
Total params: 1,972
Trainable params: 1,972
Non-trainable params: 0
_________________________________________________________________
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_7 (Dense)              (None, 48)                1776      
_________________________________________________________________
dense_8 (Dense)              (None, 4)                 196       
Total params: 1,972
Trainable params: 1,972
Non-trainable params: 0
_________________________________________________________________
3 4 24 -- 2 1 -- 0 0 -- 6 3 24
episode: 0/10000, score: 0
0
[0.00028484]

3 8 28 -- 1 2 -- 1 0 -- 5 2 28
5 2 28 -- 3 0 -- 1 0 -- 2 0 28
2 0 28 -- 3 1 -- 1 0 -- 8 2 28
8 2 28 -- 0 3 -- 1 0 -- 6 8 28
6 8 28 -- 0 3 -- 1 0 -- 7 5 28
7 5 28 -- 3 3 -- 1 0 -- 4 2 28
4 2 28 -- 3 3 -- 0 1 -- 1 8 28
episode: 32/10000, score: 6
[0.00494374]
[0.02327819]
0.36363636363636365
*******************************
0 2 32 -- 1 3 -- 1 0 -- 2 8 32
2 8 32 -- 0 3 -- 0 0 -- 0 5 32
episode: 33/10000, score: 1
[0.00543873]
[0.02364845]
0.35294117647058826
*******************************
6 4 30 -- 0 3 -- 1 0 -- 7 1 30
7 1 30 -- 3 3 -- 1 0 -- 4 7 30
4 7 30 -- 0 3 -- 1 0 -- 5 4 30
5 4 30 -- 0 3 -- 0 1 -- 3 1 30
episode: 34/10000, score: 3
[0.00722372]
[0.02429899]
0.37142857142857144
*******************************
0 1 29 -- 0 0 -- 0 0 -- 1 2 29
episode: 35/10000, score: 0
[0.00731124]
[0.0244692]
0.3611111111111111
*******************************
4 5 19 -- 0 3 -- 1 0 -- 5 2 19
5 2 19 -- 2 3 -- 1 0 -- 8 8 19
8 8 19 -- 0 1 -- 1 0 -- 6 7 19
6 7 19 -- 3 3 -- 1 0 -- 3 4 19
3 4 19 -- 0 3 -- 0 1

6 6 23 -- 3 0 -- 1 0 -- 3 7 23
3 7 23 -- 3 3 -- 1 0 -- 0 4 23
0.39436619718309857
*******************************
4 7 24 -- 3 0 -- 1 0 -- 1 8 24
1 8 24 -- 0 0 -- 0 1 -- 2 6 24
episode: 71/10000, score: 1
[0.03810688]
[0.06544516]
0.4027777777777778
*******************************
5 6 34 -- 3 3 -- 1 0 -- 2 3 34
2 3 34 -- 3 3 -- 1 0 -- 8 0 34
8 0 34 -- 3 3 -- 1 0 -- 5 6 34
5 6 34 -- 1 3 -- 1 0 -- 4 3 34
4 3 34 -- 3 3 -- 1 0 -- 1 0 34
1 0 34 -- 3 3 -- 0 1 -- 7 6 34
episode: 72/10000, score: 5
[0.03607539]
[0.06493459]
0.410958904109589
*******************************
6 5 29 -- 3 3 -- 0 0 -- 3 2 29
episode: 73/10000, score: 0
[0.03586036]
[0.06498755]
0.40540540540540543
*******************************
7 0 30 -- 3 3 -- 1 0 -- 4 6 30
4 6 30 -- 3 3 -- 0 0 -- 1 3 30
episode: 74/10000, score: 1
[0.03564364]
[0.06481144]
0.4
*******************************
1 6 20 -- 0 2 -- 0 0 -- 2 0 20
episode: 75/10000, score: 0
[0.03578402]
[0.06473216]
0.39473684210526316
*******************************
2 3

5 0 24 -- 3 2 -- 1 0 -- 2 3 24
2 3 24 -- 0 3 -- 1 0 -- 0 0 24
0 0 24 -- 3 3 -- 0 0 -- 6 6 24
episode: 104/10000, score: 8
[0.06295737]
[0.09569703]
0.3523809523809524
*******************************
2 7 22 -- 3 3 -- 0 1 -- 8 4 22
episode: 105/10000, score: 0
[0.06341743]
[0.09623032]
0.3584905660377358
*******************************
3 0 29 -- 3 3 -- 1 0 -- 0 6 29
0 6 29 -- 0 3 -- 1 0 -- 1 3 29
1 3 29 -- 3 3 -- 1 0 -- 7 0 29
7 0 29 -- 3 3 -- 1 0 -- 4 6 29
4 6 29 -- 3 3 -- 1 0 -- 1 3 29
1 3 29 -- 3 3 -- 1 0 -- 7 0 29
7 0 29 -- 3 0 -- 1 0 -- 4 1 29
4 1 29 -- 2 0 -- 0 0 -- 7 2 29
episode: 106/10000, score: 7
[0.06398486]
[0.09746592]
0.35514018691588783
*******************************
1 8 21 -- 0 0 -- 1 0 -- 2 6 21
2 6 21 -- 3 0 -- 1 0 -- 8 7 21
8 7 21 -- 3 3 -- 1 0 -- 5 4 21
5 4 21 -- 3 0 -- 1 0 -- 2 5 21
2 5 21 -- 3 0 -- 0 1 -- 8 3 21
episode: 107/10000, score: 4
[0.06554302]
[0.10001425]
0.3611111111111111
*******************************
1 0 34 -- 0 3 -- 1 0 -- 2 6 34
2 6 34 -- 3 3 -- 

1 0 33 -- 3 3 -- 0 0 -- 7 6 33
episode: 141/10000, score: 2
[0.10054579]
[0.1368429]
0.39436619718309857
*******************************
1 3 33 -- 0 3 -- 1 0 -- 2 0 33
2 0 33 -- 3 3 -- 0 0 -- 8 6 33
episode: 142/10000, score: 1
[0.10111157]
[0.13754673]
0.3916083916083916
*******************************
5 6 20 -- 3 1 -- 0 0 -- 2 8 20
episode: 143/10000, score: 0
[0.10173646]
[0.13795386]
0.3888888888888889
*******************************
4 1 24 -- 3 0 -- 1 0 -- 1 2 24
1 2 24 -- 3 3 -- 1 0 -- 7 8 24
7 8 24 -- 3 0 -- 0 1 -- 4 6 24
episode: 144/10000, score: 2
[0.10372292]
[0.14013173]
0.3931034482758621
*******************************
2 5 27 -- 3 0 -- 1 0 -- 8 3 27
8 3 27 -- 3 3 -- 0 0 -- 5 0 27
episode: 145/10000, score: 1
[0.10426971]
[0.14088894]
0.3904109589041096
*******************************
6 8 32 -- 3 3 -- 0 0 -- 3 5 32
episode: 146/10000, score: 0
[0.10454169]
[0.14146368]
0.3877551020408163
*******************************
0 5 35 -- 3 3 -- 1 0 -- 6 2 35
6 2 35 -- 3 3 -- 0 0 --

...

7 8 30 -- 0 0 -- 1 0 -- 8 6 30
8 6 30 -- 3 0 -- 1 0 -- 5 7 30
5 7 30 -- 3 3 -- 1 0 -- 2 4 30
2 4 30 -- 0 0 -- 1 0 -- 0 5 30
0 5 30 -- 2 0 -- 0 0 -- 3 3 30
episode: 9785/10000, score: 4
[1.7723867]
[1.7790661]
0.28336398937257307
*******************************
7 8 30 -- 0 0 -- 1 0 -- 8 6 30
8 6 30 -- 3 0 -- 1 0 -- 5 7 30
5 7 30 -- 3 3 -- 1 0 -- 2 4 30
2 4 30 -- 0 0 -- 1 0 -- 0 5 30
0 5 30 -- 2 0 -- 0 0 -- 3 3 30
episode: 9786/10000, score: 4
[1.771707]
[1.7783383]
0.28333503627260653
*******************************
1 8 24 -- 0 3 -- 1 0 -- 2 5 24
2 5 24 -- 0 3 -- 1 0 -- 0 2 24
0 2 24 -- 3 3 -- 0 0 -- 6 8 24
episode: 9787/10000, score: 2
[1.7712222]
[1.7780288]
0.28330608908868
*******************************
3 6 18 -- 3 0 -- 0 0 -- 0 7 18
episode: 9788/10000, score: 0
[1.7710803]
[1.7778851]
0.2832771478189805
*******************************
1 3 18 -- 0 0 -- 1 0 -- 2 4 18
2 4 18 -- 0 0 -- 0 0 -- 0 5 18
episode: 9789/10000, score: 1
[1.7707845]
[1.777597]
0.2832482124616956
*************

7 0 19 -- 0 3 -- 1 0 -- 8 6 19
8 6 19 -- 3 0 -- 1 0 -- 5 7 19
5 7 19 -- 3 3 -- 1 0 -- 2 4 19
2 4 19 -- 0 0 -- 1 0 -- 0 5 19
0 5 19 -- 0 3 -- 0 0 -- 1 2 19
episode: 9833/10000, score: 4
[1.758861]
[1.7658126]
0.28248932275777916
*******************************
1 7 27 -- 0 2 -- 1 0 -- 2 1 27
2 1 27 -- 0 0 -- 0 1 -- 0 2 27
episode: 9834/10000, score: 1
[1.7597435]
[1.7667825]
0.2825622775800712
*******************************
0 8 25 -- 3 3 -- 1 0 -- 6 5 25
6 5 25 -- 0 3 -- 0 0 -- 7 2 25
episode: 9835/10000, score: 1
[1.7592498]
[1.766262]
0.28253355022366816
*******************************
0 4 23 -- 3 0 -- 0 1 -- 6 5 23
episode: 9836/10000, score: 0
[1.7591039]
[1.7660844]
0.2826064857171902
*******************************
5 7 26 -- 3 2 -- 1 0 -- 2 1 26
2 1 26 -- 3 0 -- 0 0 -- 8 2 26
episode: 9837/10000, score: 1
[1.7588211]
[1.7657366]
0.28257775970725757
*******************************
3 5 35 -- 3 3 -- 1 0 -- 0 2 35
0 2 35 -- 2 3 -- 0 0 -- 3 8 35
episode: 9838/10000, score: 1
[1.7583536

1 4 29 -- 0 0 -- 0 1 -- 2 5 29
episode: 9879/10000, score: 0
[1.7547967]
[1.7615497]
0.2823886639676113
*******************************
7 0 35 -- 2 3 -- 1 0 -- 1 6 35
1 6 35 -- 0 0 -- 1 0 -- 2 7 35
2 7 35 -- 0 3 -- 1 0 -- 0 4 35
0 4 35 -- 2 0 -- 1 0 -- 3 5 35
3 5 35 -- 3 3 -- 1 0 -- 0 2 35
0 2 35 -- 2 3 -- 0 0 -- 3 8 35
episode: 9880/10000, score: 5
[1.7537966]
[1.7604653]
0.2823600850116385
*******************************
3 1 32 -- 3 0 -- 1 0 -- 0 2 32
0 2 32 -- 2 2 -- 0 0 -- 3 5 32
episode: 9881/10000, score: 1
[1.7534248]
[1.7601537]
0.28233151183970856
*******************************
7 5 28 -- 0 1 -- 1 0 -- 8 4 28
8 4 28 -- 0 3 -- 0 0 -- 6 1 28
episode: 9882/10000, score: 1
[1.7531488]
[1.7598591]
0.28230294445006576
*******************************
0 7 30 -- 0 3 -- 1 0 -- 1 4 30
1 4 30 -- 0 0 -- 1 0 -- 2 5 30
2 5 30 -- 0 0 -- 0 0 -- 0 3 30
episode: 9883/10000, score: 2
[1.752694]
[1.7594498]
0.2822743828409551
*******************************
1 5 20 -- 0 3 -- 0 0 -- 2 2 20
episode: 

2 7 26 -- 3 3 -- 0 0 -- 8 4 26
episode: 9925/10000, score: 2
[1.7362453]
[1.74245]
0.28138222849083216
*******************************
8 7 22 -- 3 0 -- 1 0 -- 5 8 22
5 8 22 -- 3 0 -- 1 0 -- 2 6 22
2 6 22 -- 0 0 -- 1 0 -- 0 7 22
0 7 22 -- 3 0 -- 1 0 -- 6 8 22
6 8 22 -- 0 0 -- 1 0 -- 7 6 22
7 6 22 -- 3 0 -- 0 0 -- 4 7 22
episode: 9926/10000, score: 5
[1.7353971]
[1.7414441]
0.28135388334844363
*******************************
6 4 28 -- 0 3 -- 0 0 -- 7 1 28
episode: 9927/10000, score: 0
[1.7351571]
[1.7412466]
0.28132554391619663
*******************************
3 5 18 -- 3 0 -- 0 0 -- 0 3 18
episode: 9928/10000, score: 0
[1.7349619]
[1.7410686]
0.2812972101923658
*******************************
4 0 24 -- 0 3 -- 0 1 -- 5 6 24
episode: 9929/10000, score: 0
[1.7356318]
[1.7419652]
0.2813695871097684
*******************************
1 0 26 -- 0 2 -- 1 0 -- 2 3 26
2 3 26 -- 3 0 -- 0 0 -- 8 4 26
episode: 9930/10000, score: 1
[1.7352663]
[1.7416189]
0.2813412546571342
*****************************

7 8 27 -- 2 0 -- 1 0 -- 1 6 27
1 6 27 -- 0 0 -- 1 0 -- 2 7 27
2 7 27 -- 0 2 -- 0 1 -- 0 1 27
episode: 9973/10000, score: 2
[1.7232597]
[1.7282962]
0.2805293763785843
*******************************
3 2 33 -- 3 3 -- 1 0 -- 0 8 33
0 8 33 -- 2 0 -- 0 0 -- 3 6 33
episode: 9974/10000, score: 1
[1.7228745]
[1.727908]
0.2805012531328321
*******************************
2 8 25 -- 0 3 -- 1 0 -- 0 5 25
0 5 25 -- 3 3 -- 1 0 -- 6 2 25
6 2 25 -- 0 3 -- 0 0 -- 7 8 25
episode: 9975/10000, score: 2
[1.7222716]
[1.7273192]
0.28047313552526065
*******************************
7 3 26 -- 0 0 -- 0 0 -- 8 4 26
episode: 9976/10000, score: 0
[1.7220703]
[1.7271272]
0.2804450235541746
*******************************
1 7 30 -- 0 3 -- 1 0 -- 2 4 30
2 4 30 -- 0 0 -- 1 0 -- 0 5 30
0 5 30 -- 2 0 -- 0 0 -- 3 3 30
episode: 9977/10000, score: 2
[1.721483]
[1.7266127]
0.2804169172178793
*******************************
1 8 34 -- 0 1 -- 0 0 -- 2 7 34
episode: 9978/10000, score: 0
[1.7212973]
[1.7264208]
0.28038881651468084

In [5]:
np.random.seed(99)
random.seed(999)
prng.seed(999)

count = 0
total = 10000
for i in range(total):
    state = game.reset()
    state = np.reshape(state, [1, state_size])
    for time in range(10):
                # env.render()
        action1 = agent1.get_maxaction(state)
        action2 = agent2.get_maxaction(state)

        next_state, reward, done = game.step(action1,action2)

                #reward = reward if not done else -10
        next_state = np.reshape(next_state, [1, state_size])  
        #print(np.where(state == 1.0)[1][0],np.where(state == 1.0)[1][1] - 9,np.where(state == 1.0)[1][2],"--",action1, action2,"--",reward[0][0],reward[1][0],"--",np.where(next_state == 1.0)[1][0],np.where(next_state == 1.0)[1][1] - 9,np.where(next_state == 1.0)[1][2])

                    #print(agent1.lam,agent2.lam)
        state = next_state
        if done:
                    #print(state)
            #print("episode: {}/{}, score: {}"
                    #.format(e, EPISODES, time))
            #print(agent1.lam)
            #print(agent2.lam)
            if reward[1][0] == 1:
                count = count+1
                
            break
                    #if len(agent.memory) > batch_size:
                        #agent.replay(batch_size)

            print('*******************************')
print(count/total)

0.1526


In [23]:
game = CoinGameVec()
state = game.reset()
print(state)
action1 = 1
action2 = 2
next_state, reward, done = game.step(action1,action2)
print(reward)
print(reward[0][0],reward[1][0])

[[[[0. 0. 0.]
   [0. 0. 1.]
   [0. 0. 0.]]

  [[0. 0. 0.]
   [0. 0. 0.]
   [0. 0. 1.]]

  [[0. 0. 0.]
   [1. 0. 0.]
   [0. 0. 0.]]

  [[0. 0. 0.]
   [0. 0. 0.]
   [0. 0. 0.]]]]
[array([0]), array([0])]
0 0


In [4]:
print(count/total)

0.2238


In [3]:
import numpy as np
int(np.divide(3,2))

1

In [7]:
np.savetxt('CGIndependent_penalty',store_penalty)
np.savetxt('CGIndependent_Lag',store_lag)

In [4]:
print(count/total)

0.1526
